In [0]:
from __future__ import absolute_import        #TURN RUNTIME FROM CPU TO GPU
from __future__ import division
from __future__ import print_function
from __future__ import unicode_literals

In [0]:
import torch
from torch.jit import script, trace
import torch.nn as nn
from torch import optim
import torch.nn.functional as F
import csv
import random
import re
import os
import unicodedata
import codecs
from io import open
import itertools
import math

In [0]:
!nvcc --version   #For Checking Version of Pre-installed CUDA 

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2019 NVIDIA Corporation
Built on Sun_Jul_28_19:07:16_PDT_2019
Cuda compilation tools, release 10.1, V10.1.243


In [0]:
use_cuda = True

In [0]:
#if use_cuda and torch.cuda.is_available():
 # net.cuda()

In [0]:
from google.colab import drive
drive.mount('/content/gdrive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/gdrive


In [0]:
root_path = 'gdrive/My Drive/ML Projects/ChatBot/cornell movie-dialogs corpus/'  

# **Data Preparation**


In [0]:
lines_filepath = os.path.join(root_path,"movie_lines.txt")
conv_filepath = os.path.join(root_path,"movie_conversations.txt")

In [0]:
with open(lines_filepath,'r', encoding="utf8", errors='ignore') as file :
  lines = file.readlines()
for line in lines[:8]:
  print(line.strip())

L1045 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ They do not!
L1044 +++$+++ u2 +++$+++ m0 +++$+++ CAMERON +++$+++ They do to!
L985 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ I hope so.
L984 +++$+++ u2 +++$+++ m0 +++$+++ CAMERON +++$+++ She okay?
L925 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ Let's go.
L924 +++$+++ u2 +++$+++ m0 +++$+++ CAMERON +++$+++ Wow
L872 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ Okay -- you're gonna need to learn how to lie.
L871 +++$+++ u2 +++$+++ m0 +++$+++ CAMERON +++$+++ No


In [0]:
line_fields = ["lineID","characterID","movieID","character","text"]    #Splits each line of file into dict of fields
lines = {}                                                             #Movie_lines.txt
with open(lines_filepath,'r', encoding='iso-8859-1') as f:
  for line in f:
    values = line.split(" +++$+++ ")
    lineObj = {}
    for i,field in enumerate(line_fields):
      lineObj[field] = values[i]
    lines[lineObj['lineID']] = lineObj

In [0]:
conv_fields = ["character1ID","character2ID","movieID","utteranceIDs"]      #Splits each line of file into dict of fields
conversations =[]                                                           #Movie_conversations.txt
with open(conv_filepath,'r',encoding='iso-8859-1')as f:
  for line in f:
    values = line.split(" +++$+++ ")
    convObj = {}
    for i, field in enumerate(conv_fields):
      convObj[field] = values[i]
    lineIDs = eval(convObj["utteranceIDs"])
    convObj["lines"] = []
    for lineID in lineIDs:
      convObj["lines"].append(lines[lineID])
    conversations.append(convObj)

In [0]:
qa_pairs = []            #Extract Pair of Convo
for conversation in conversations:
  for i in range(len(conversation["lines"])-1):
    inputLine = conversation["lines"][i]["text"].strip()
    targetLine = conversation["lines"][i+1]["text"].strip()
    if inputLine and targetLine:
      qa_pairs.append([inputLine, targetLine])

In [0]:
datafile = os.path.join(root_path, "formatted_movie_lines.txt")
delimiter = '\t'
delimiter = str(codecs.decode(delimiter,"unicode_escape"))
print("Start")
with open(datafile,'w', encoding='utf-8') as outputfile:
  writer = csv.writer(outputfile, delimiter = delimiter)
  for pair in qa_pairs:
    writer.writerow(pair)
print("Done writing!")

Start
Done writing!


In [0]:
datafile = os.path.join(root_path,"formatted_movie_lines.txt")
with open(datafile,'rb') as file:
  lines = file.readlines()
for line in lines[:5]:
  print(line)

b"Can we make this quick?  Roxanne Korrine and Andrew Barrett are having an incredibly horrendous public break- up on the quad.  Again.\tWell, I thought we'd start with pronunciation, if that's okay with you.\r\n"
b"Well, I thought we'd start with pronunciation, if that's okay with you.\tNot the hacking and gagging and spitting part.  Please.\r\n"
b"Not the hacking and gagging and spitting part.  Please.\tOkay... then how 'bout we try out some French cuisine.  Saturday?  Night?\r\n"
b"You're asking me out.  That's so cute. What's your name again?\tForget it.\r\n"
b"No, no, it's my fault -- we didn't have a proper introduction ---\tCameron.\r\n"


In [0]:
PAD_token = 0       #Padding Short Sentences
SOS_token = 1       #Start Of Sentence token
EOS_token = 2       #End Of Sentence token
class Vocabulary:
  def __init__(self,name):
    self.name = name
    self.word2index = {}
    self.word2count = {}
    self.index2word = {PAD_token: "PAD", SOS_token: "SOS", EOS_token: "EOS"}
    self.num_words = 3
  
  def addSentence(self, sentence):
    for word in sentence.split(' '):
      self.addWord(word)
  
  def addWord(self, word):
    if word not in self.word2index:
      self.word2index[word] = self.num_words
      self.word2count[word] = 1
      self.index2word[self.num_words] = word
      self.num_words += 1
    else:
      self.word2count[word] += 1
  
  def trim(self, min_count):         # Removing words below a certain threshold
    keep_words = []
    for k,v in self.word2count.items():
      if v>= min_count:
        keep_words.append(k)
    
    print('keep words {} / {} = {:.4f}'.format(len(keep_words),len(self.word2index), len(keep_words) / len(self.word2index)))
    self.word2index = {}
    self.word2count = {}
    self.index2word = {PAD_token:"PAD", SOS_token:"SOS", EOS_token:"EOS"}
    self.num_words = 3

    for word in keep_words:
      self.addWord(word)

In [0]:
def unicodeToAscii(s):    # Turn unicode string to plain ASCII
  return ''.join(c for c in unicodedata.normalize('NFD',s) if unicodedata.category(c) != 'Mn')

In [0]:
def normalizeString(s):        # Lowercase, trim white spaces, and remove non-letter characters
  s = unicodeToAscii(s.lower().strip())
  s = re.sub(r"([.!?])", r" \1", s)
  s = re.sub(r"[^a-zA-Z.!?]+", r" ", s)
  s = re.sub(r"\s+", r" ", s).strip()
  return s

In [0]:
normalizeString("aa123aa!s's  dd?")

'aa aa !s s dd ?'

In [0]:
datafile = os.path.join(root_path, "formatted_movie_lines.txt")
print("Reading and Processing")
lines = open(datafile, encoding='utf-8').read().strip().split('\n')
pairs = [[normalizeString(s) for s in pair.split('\t')] for pair in lines]
voc = Vocabulary("cornell movie-dialogs corpus")

Reading and Processing


In [0]:
MAX_LENGTH = 10                             #Max Sentence length to consider
def filterPair(p):
  return len(p[0].split()) < MAX_LENGTH and len(p[1].split()) < MAX_LENGTH

def filterPairs(pairs):
  return [pair for pair in pairs if filterPair(pair)]

save_dir = os.path.join(root_path, "save")

In [0]:
pairs = [pair for pair in pairs if len(pair)>1]
print("There are {} pairs/conversations in the dataset".format(len(pairs)))
pairs = filterPairs(pairs)
print("After filter there are {} pairs".format(len(pairs)))

There are 221282 pairs/conversations in the dataset
After filter there are 64271 pairs


In [0]:
for pair in pairs:
  voc.addSentence(pair[0])
  voc.addSentence(pair[1])
print("Counted Words", voc.num_words)
for pair in pairs[:10]:
  print(pair)

Counted Words 18008
['there .', 'where ?']
['you have my word . as a gentleman', 'you re sweet .']
['hi .', 'looks like things worked out tonight huh ?']
['you know chastity ?', 'i believe we share an art instructor']
['have fun tonight ?', 'tons']
['well no . . .', 'then that s all you had to say .']
['then that s all you had to say .', 'but']
['but', 'you always been this selfish ?']
['do you listen to this crap ?', 'what crap ?']
['what good stuff ?', 'the real you .']


In [0]:
MIN_COUNT = 3
def trimRareWords(voc, pairs, MIN_COUNT):
    voc.trim(MIN_COUNT)
    keep_pairs = []
    for pair in pairs:
      input_sentence = pair[0]
      output_sentence = pair[1]
      keep_input = True
      keep_output = True
      for word in input_sentence.split(' '):
        if word not in voc.word2index:
          keep_input = False
          break

      for word in output_sentence.split(' '):
        if word not in voc.word2index:
          keep_output = False
          break

      if keep_input and keep_output:
        keep_pairs.append(pair)
    print(len(keep_pairs))
    return keep_pairs

pairs = trimRareWords(voc, pairs, MIN_COUNT)

keep words 7823 / 18005 = 0.4345
53165


In [0]:
def indexesFromSentence(voc, sentence):
  return [voc.word2index[word] for word in sentence.split(' ')] + [EOS_token]

In [0]:
indexesFromSentence(voc, pairs[1][0])   # TEST    EOS_token = 2 that's why we'll have 2 at the end 

[7, 8, 9, 10, 4, 11, 12, 13, 2]

In [0]:
pairs[1][0]

'you have my word . as a gentleman'

In [0]:
inp = []
out = []
for pair in pairs[:10]:
  inp.append(pair[0])
  out.append(pair[1])
print(inp)
print(len(inp))
indexes = [indexesFromSentence(voc, sentence) for sentence in inp]
indexes

['there .', 'you have my word . as a gentleman', 'hi .', 'have fun tonight ?', 'well no . . .', 'then that s all you had to say .', 'but', 'do you listen to this crap ?', 'what good stuff ?', 'wow']
10


[[3, 4, 2],
 [7, 8, 9, 10, 4, 11, 12, 13, 2],
 [16, 4, 2],
 [8, 31, 22, 6, 2],
 [33, 34, 4, 4, 4, 2],
 [35, 36, 37, 38, 7, 39, 40, 41, 4, 2],
 [42, 2],
 [47, 7, 48, 40, 45, 49, 6, 2],
 [50, 51, 52, 6, 2],
 [58, 2]]

In [0]:
def zeroPadding(l, fillvalue = 0):
  return list(itertools.zip_longest(*l, fillvalue=fillvalue ))

In [0]:
leng = [len(ind) for ind in indexes]
max(leng)

10

In [0]:
test_result = zeroPadding(indexes)     # TEST
print(test_result)   

[(3, 7, 16, 8, 33, 35, 42, 47, 50, 58), (4, 8, 4, 31, 34, 36, 2, 7, 51, 2), (2, 9, 2, 22, 4, 37, 0, 48, 52, 0), (0, 10, 0, 6, 4, 38, 0, 40, 6, 0), (0, 4, 0, 2, 4, 7, 0, 45, 2, 0), (0, 11, 0, 0, 2, 39, 0, 49, 0, 0), (0, 12, 0, 0, 0, 40, 0, 6, 0, 0), (0, 13, 0, 0, 0, 41, 0, 2, 0, 0), (0, 2, 0, 0, 0, 4, 0, 0, 0, 0), (0, 0, 0, 0, 0, 2, 0, 0, 0, 0)]


In [0]:
def binaryMatrix(l, value=0):
  m = []
  for i, seq in enumerate(l):
    m.append([])
    for token in seq:
      if token == PAD_token:
        m[i].append(0)
      else:
        m[i].append(1)
  return m

In [0]:
binary_result = binaryMatrix(test_result)      # TEST
binary_result

[[1, 1, 1, 1, 1, 1, 1, 1, 1, 1],
 [1, 1, 1, 1, 1, 1, 1, 1, 1, 1],
 [1, 1, 1, 1, 1, 1, 0, 1, 1, 0],
 [0, 1, 0, 1, 1, 1, 0, 1, 1, 0],
 [0, 1, 0, 1, 1, 1, 0, 1, 1, 0],
 [0, 1, 0, 0, 1, 1, 0, 1, 0, 0],
 [0, 1, 0, 0, 0, 1, 0, 1, 0, 0],
 [0, 1, 0, 0, 0, 1, 0, 1, 0, 0],
 [0, 1, 0, 0, 0, 1, 0, 0, 0, 0],
 [0, 0, 0, 0, 0, 1, 0, 0, 0, 0]]

In [0]:
def inputVar(l,voc):        #Returns padded input sequence tensor and tensor of lengths for each of the sequence in the batch
  indexes_batch = [indexesFromSentence(voc, sentence) for sentence in l]
  lengths = torch.tensor([len(indexes) for indexes in indexes_batch])
  padList = zeroPadding(indexes_batch)
  padVar = torch.LongTensor(padList)
  return padVar, lengths

In [0]:
def outputVar(l, voc):       #Returns padded target sequence tensor, padding mask and max target length
  indexes_batch = [indexesFromSentence(voc, sentence) for sentence in l]
  max_target_len = max([len(indexes) for indexes in indexes_batch])
  padList = zeroPadding(indexes_batch)
  mask = binaryMatrix(padList)
  mask = torch.ByteTensor(mask)
  padVar = torch.LongTensor(padList)
  return padVar, mask, max_target_len

In [0]:
def batch2TrainData(voc, pair_batch):       #Returns all items for a given batch of pairs
  pair_batch.sort(key=lambda x: len(x[0].split(" ")),reverse=True)
  input_batch, output_batch = [], []
  for pair in pair_batch:
    input_batch.append(pair[0])
    output_batch.append(pair[1])
  inp, lengths = inputVar(input_batch, voc)
  output, mask, max_target_len = outputVar(output_batch, voc)
  return inp, lengths, output, mask, max_target_len

In [0]:
# EXAMPLE FOR VALIDTION
small_batch_size = 5
batches = batch2TrainData(voc, [random.choice(pairs) for _ in range(small_batch_size)])
input_variable, lengths, target_variable, mask, max_target_len = batches

print("input variable: ",input_variable)      #batch X length for matrix
print("lengths: ",lengths)
print("target variable: ",target_variable)
print("mask: ",mask)
print("max target length: ",max_target_len)

input variable:  tensor([[ 188,  124,  112,  557,  101],
        [ 835,  601, 3883,    7,   37],
        [ 101,    7,   83,   50, 1418],
        [ 191,  509,    4,    6,    4],
        [ 117,  218,    4,    2,    2],
        [ 156,   36,    4,    0,    0],
        [ 447,    6,    2,    0,    0],
        [   4,    2,    0,    0,    0],
        [   2,    0,    0,    0,    0]])
lengths:  tensor([9, 8, 7, 5, 5])
target variable:  tensor([[ 122,   50,   25,   36,   98],
        [  36,    6,  356,    7,   12],
        [ 782,    2,    7,   14,   69],
        [   7,    0,  997,   67,    4],
        [1026,    0,    4,  375,    2],
        [ 488,    0,    2,    4,    0],
        [   6,    0,    0,    2,    0],
        [   2,    0,    0,    0,    0]])
mask:  tensor([[1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1],
        [1, 0, 1, 1, 1],
        [1, 0, 1, 1, 1],
        [1, 0, 1, 1, 0],
        [1, 0, 0, 1, 0],
        [1, 0, 0, 0, 0]], dtype=torch.uint8)
max target length:  8


**MODEL**

In [0]:
class EncoderRNN(nn.Module):
  def __init__(self, hidden_size, embedding, n_layers=1, dropout=0):
    super(EncoderRNN, self).__init__()
    self.n_layers = n_layers
    self.hidden_size = hidden_size
    self.embedding = embedding
    # Initialize GRU; the input_size and hidden_size params are both set to 'hidden_size'
    # because our input size is a word embedding with number of features == hidden_size
    self.gru = nn.GRU(hidden_size, hidden_size, n_layers, dropout = (0 if n_layers == 1 else dropout), bidirectional=True)

  def forward(self, input_seq, input_lengths, hidden=None):
    # input_seq: batch of input sentences; shape(max_length, batch_size)
    # input_lengths: list of sentence lengths corresponding to each sentence in the batch
    # hidden state of shape: (n_layers x num_directions, batch_size, hidden_size)
    # Convert word indexes to embeddings
    embedded = self.embedding(input_seq)
    # Pack padded batch of sequences for RNN module
    packed = torch.nn.utils.rnn.pack_padded_sequence(embedded, input_lengths)
    # Forward pass through GRU
    outputs, hidden = self.gru(packed, hidden)
    # Unpack padding
    outputs, _ = torch.nn.utils.rnn.pad_packed_sequence(outputs)
    # Sum bidirectional GRU outputs
    outputs = outputs[:, :, :self.hidden_size] + outputs[:, :, self.hidden_size:]
    # Return output and final hidden state 
    return outputs, hidden
    # outputs: the output features h_t from the last layer of the GRU, for each timestep (sum of bidirectional outputs)
    # outputs shape = (max_length,batch_size, hidden_size)
    # hidden: hidden state for the last timestep, of shape=(n_layers x num_direactions, batch_size, hidden_size)

In [0]:
class Attn(torch.nn.Module):
  def __init__(self, method, hidden_size):
    super(Attn, self).__init__()
    self.method = method
    self.hidden_size = hidden_size

  def dot_score(self, hidden, encoder_output):
    # Element-Wise multiply the current target decoder state with the encoder output and sum time
    return torch.sum(hidden * encoder_output, dim=2)
  
  def forward(self, hidden, encoder_outputs):
    # hidden of shape: (1, batch_size, hidden_size)
    # encoder_outputs of shape: (max_length, batch_size, hidden_size)
    # Calculate the attention weights(energies)
    attn_energies = self.dot_score(hidden, encoder_outputs)   # (max_length, batch_size)
    # Transpose max_length and batch_size dimensions
    attn_energies = attn_energies.t()                         # (batch_size, max_length)
    # Return the softmax normalized probability scores (with added dimension)
    return F.softmax(attn_energies, dim=1).unsqueeze(1)       # (batch_size, 1, max_length)

In [0]:
class LAttnDecoderRNN(nn.Module):
  def __init__(self, attn_model, embedding, hidden_size, output_size, n_layers=1, dropout=0.1):
    super(LAttnDecoderRNN, self).__init__()
    self.attn_model = attn_model
    self.hidden_size = hidden_size
    self.output_size = output_size
    self.n_layers = n_layers
    self.dropout = dropout

    # Define Layers
    self.embedding = embedding
    self.embedding_dropout = nn.Dropout(dropout)
    self.gru = nn.GRU(hidden_size, hidden_size, n_layers, dropout=(0 if n_layers == 1 else dropout))
    self.concat = nn.Linear(hidden_size * 2, hidden_size)
    self.out = nn.Linear(hidden_size, output_size)

    self.attn = Attn(attn_model, hidden_size)

  def forward(self, input_step, last_hidden, encoder_outputs):
    # Input_step: one timestep(one word) of input sequence batch; shape(1, batch_size)
    # last_hidden: final hidden layer of GRU; shape=(n_layers x num_diractions, batch_size, hidden_size)
    # encoder_outputs: encoder model's output; shape=(max_length, batch_size, hidden_size)
    # We run this one step(word) at a time

    #Get embedding of current input word
    embedded = self.embedding(input_step)
    embedded = self.embedding_dropout(embedded)
    # Forward through bidirectional GRU
    rnn_output, hidden = self.gru(embedded, last_hidden)
    # Calculate attention weights from the current GRU output
    attn_weights = self.attn(rnn_output, encoder_outputs)
    # Multiply attention weights to encoder outputs to get new "weighted sum" context vector
    # (batch_size, 1, max_length) bmm with (batch_size, max_length, hidden) = (batch_size, 1, hidden)
    context = attn_weights.bmm(encoder_outputs.transpose(0, 1))
    # Concatenate weighted context vector and GRU output
    rnn_output = rnn_output.squeeze(0)
    context = context.squeeze(1)
    concat_input = torch.cat((rnn_output, context), 1)
    concat_output = torch.tanh(self.concat(concat_input))
    # Predict next word 
    output = self.out(concat_output)
    output = F.softmax(output, dim=1)
    # Return output and final hidden state
    return output, hidden
    # output: Softmax normalised tensor giving probablities of each word being the  correct next word in decoded seq
    # shape = (batch_size, voc.num_words)
    # hidden = final hidden state of GRU; shape=(n_layers x num_directions, batch_size, hidden_size)

**Training**

In [0]:
def maskNLoss(inp, target, mask):
  nTotal = mask.sum()
  crossEntropy = -torch.log(torch.gather(inp, 1, target.view(-1, 1)).squeeze(1))
  #target = target.view(-1,1)
  # decoder_out shape: (batch_size, vocab_size), target_szie = (batch_size, 1)
  #gathered_tensor = torch.gather(decoder_out, 1, target)
  # Calculate the (-)ve log likelihood loss
  #crossEntropy = -torch.log(gathered_tensor)
  # select the non-zero elements
  loss = crossEntropy.masked_select(mask)
  #calculate mean od loss
  loss = loss.mean()
  loss = loss.to(device)
  return loss, nTotal.item()

In [0]:
def train(input_variable, lengths, target_variable, mask, max_target_len, encoder, decoder, embedding, encoder_optimizer, decoder_optimizer, batch_size, clip, max_length=MAX_LENGTH):

  #Zero gradients
  encoder_optimizer.zero_grad()
  decoder_optimizer.zero_grad()

  #Set Device options
  input_variable = input_variable.to(device)
  lengths = lengths.to(device)
  target_variable = target_variable.to(device)
  mask = mask.to(device)

  #Initialize Variables
  loss = 0
  print_losses = []
  n_totals = 0

  #Forward pass through encoder
  encoder_outputs, encoder_hidden = encoder(input_variable, lengths)

  decoder_input = torch.LongTensor([[SOS_token for _ in range(batch_size)]])
  decoder_input = decoder_input.to(device)

  decoder_hidden = encoder_hidden[:decoder.n_layers]

  use_teacher_forcing = True if random.random() < teacher_forcing_ratio else False

  if use_teacher_forcing:
    for t in range(max_target_len):
      decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden, encoder_outputs)
      decoder_input = target_variable[t].view(1,-1)
      mask_loss, nTotal = maskNLoss(decoder_output, target_variable[t], mask[t])
      loss += mask_loss
      print_losses.append(mask_loss.items() * nTotal)
      n_totals += nTotal 
  else:
    for t in range(max_target_len):
      decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden, encoder_outputs)
      _, topi = decoder_output.topk(1)
      decoder_input = torch.LongTensor([[topi[i][0] for i in range(batch_size)]])
      decoder_input = decoder_input.to(device)
      mask_loss, nTotal = maskNLose(decoder_output, target_variable[t], mask[t])
      loss += mask_loss
      print_losses.append(mask_loss.item() * nTotal)
      n_totals += nTotal

  loss.backward()

  _ = torch.nn.utils.clip_grad_norm_(encoder.parameters(), clip)
  _ = torch.nn.utils.clip_grad_norm_(decoder.parameters(), clip)

  encoder_optimizer.step()
  decoder_optimizer.step()

  return sum(print_losses) / n_totals


In [0]:
def trainIters(model_name, voc, pairs, encoder, decoder, encoder_optimizer, decoder_optimizer, embedding, encoder_n_layers, decoder_n_layers, save_dir, n_iteration, batch_size, print_every, save_every, clip, corpus_name, loadFilename):

    # Load batches for each iteration
    training_batches = [batch2TrainData(voc, [random.choice(pairs) for _ in range(batch_size)])
                      for _ in range(n_iteration)]

    # Initializations
    print('Initializing ...')
    start_iteration = 1
    print_loss = 0
    if loadFilename:
        start_iteration = checkpoint['iteration'] + 1

    # Training loop
    print("Training...")
    for iteration in range(start_iteration, n_iteration + 1):
        training_batch = training_batches[iteration - 1]
        # Extract fields from batch
        input_variable, lengths, target_variable, mask, max_target_len = training_batch

        # Run a training iteration with batch
        loss = train(input_variable, lengths, target_variable, mask, max_target_len, encoder,
                     decoder, embedding, encoder_optimizer, decoder_optimizer, batch_size, clip)
        print_loss += loss

        # Print progress
        if iteration % print_every == 0:
            print_loss_avg = print_loss / print_every
            print("Iteration: {}; Percent complete: {:.1f}%; Average loss: {:.4f}".format(iteration, iteration / n_iteration * 100, print_loss_avg))
            print_loss = 0

        # Save checkpoint
        if (iteration % save_every == 0):
            directory = os.path.join(save_dir, model_name, corpus_name, '{}-{}_{}'.format(encoder_n_layers, decoder_n_layers, hidden_size))
            if not os.path.exists(directory):
                os.makedirs(directory)
            torch.save({
                'iteration': iteration,
                'en': encoder.state_dict(),
                'de': decoder.state_dict(),
                'en_opt': encoder_optimizer.state_dict(),
                'de_opt': decoder_optimizer.state_dict(),
                'loss': loss,
                'voc_dict': voc.__dict__,
                'embedding': embedding.state_dict()
            }, os.path.join(directory, '{}_{}.tar'.format(iteration, 'checkpoint')))


In [0]:
class GreedySearchDecoder(nn.Module):
    def __init__(self, encoder, decoder):
        super(GreedySearchDecoder, self).__init__()
        self.encoder = encoder
        self.decoder = decoder

    def forward(self, input_seq, input_length, max_length):
        # Forward input through encoder model
        encoder_outputs, encoder_hidden = self.encoder(input_seq, input_length)
        # Prepare encoder's final hidden layer to be first hidden input to the decoder
        decoder_hidden = encoder_hidden[:decoder.n_layers]
        # Initialize decoder input with SOS_token
        decoder_input = torch.ones(1, 1, device=device, dtype=torch.long) * SOS_token
        # Initialize tensors to append decoded words to
        all_tokens = torch.zeros([0], device=device, dtype=torch.long)
        all_scores = torch.zeros([0], device=device)
        # Iteratively decode one word token at a time
        for _ in range(max_length):
            # Forward pass through decoder
            decoder_output, decoder_hidden = self.decoder(decoder_input, decoder_hidden, encoder_outputs)
            # Obtain most likely word token and its softmax score
            decoder_scores, decoder_input = torch.max(decoder_output, dim=1)
            # Record token and score
            all_tokens = torch.cat((all_tokens, decoder_input), dim=0)
            all_scores = torch.cat((all_scores, decoder_scores), dim=0)
            # Prepare current token to be next decoder input (add a dimension)
            decoder_input = torch.unsqueeze(decoder_input, 0)
        # Return collections of word tokens and scores
        return all_tokens, all_scores


In [0]:
def evaluate(encoder, decoder, searcher, voc, sentence, max_length=MAX_LENGTH):
    ### Format input sentence as a batch
    # words -> indexes
    indexes_batch = [indexesFromSentence(voc, sentence)]
    # Create lengths tensor
    lengths = torch.tensor([len(indexes) for indexes in indexes_batch])
    # Transpose dimensions of batch to match models' expectations
    input_batch = torch.LongTensor(indexes_batch).transpose(0, 1)
    # Use appropriate device
    input_batch = input_batch.to(device)
    lengths = lengths.to(device)
    # Decode sentence with searcher
    tokens, scores = searcher(input_batch, lengths, max_length)
    # indexes -> words
    decoded_words = [voc.index2word[token.item()] for token in tokens]
    return decoded_words


def evaluateInput(encoder, decoder, searcher, voc):
    input_sentence = ''
    while(1):
        try:
            # Get input sentence
            input_sentence = input('> ')
            # Check if it is quit case
            if input_sentence == 'q' or input_sentence == 'quit': break
            # Normalize sentence
            input_sentence = normalizeString(input_sentence)
            # Evaluate sentence
            output_words = evaluate(encoder, decoder, searcher, voc, input_sentence)
            # Format and print response sentence
            output_words[:] = [x for x in output_words if not (x == 'EOS' or x == 'PAD')]
            print('Bot:', ' '.join(output_words))

        except KeyError:
            print("Error: Encountered unknown word.")


In [0]:
model_name = 'cb_model'
attn_model = 'dot'
#attn_model = 'general'
#attn_model = 'concat'
hidden_size = 500
encoder_n_layers = 2
decoder_n_layers = 2
dropout = 0.1
batch_size = 128

# Set checkpoint to load from; set to None if starting from scratch
loadFilename = None
checkpoint_iter = 3500
#loadFilename = os.path.join(save_dir, model_name, corpus_name,
#                            '{}-{}_{}'.format(encoder_n_layers, decoder_n_layers, hidden_size),
#                            '{}_checkpoint.tar'.format(checkpoint_iter))


# Load model if a loadFilename is provided
if loadFilename:
    # If loading on same machine the model was trained on
    #checkpoint = torch.load(loadFilename)
    # If loading a model trained on GPU to CPU
    checkpoint = torch.load(loadFilename, map_location=torch.device('cpu'))
    encoder_sd = checkpoint['en']
    decoder_sd = checkpoint['de']
    encoder_optimizer_sd = checkpoint['en_opt']
    decoder_optimizer_sd = checkpoint['de_opt']
    embedding_sd = checkpoint['embedding']
    voc.__dict__ = checkpoint['voc_dict']


print('Building encoder and decoder ...')
# Initialize word embeddings
embedding = nn.Embedding(voc.num_words, hidden_size)
if loadFilename:
    embedding.load_state_dict(embedding_sd)
# Initialize encoder & decoder models
encoder = EncoderRNN(hidden_size, embedding, encoder_n_layers, dropout)
decoder = LAttnDecoderRNN(attn_model, embedding, hidden_size, voc.num_words, decoder_n_layers, dropout)
if loadFilename:
    encoder.load_state_dict(encoder_sd)
    decoder.load_state_dict(decoder_sd)
# Use appropriate device
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
encoder = encoder.to(device)
decoder = decoder.to(device)
print('Models built and ready to go!')

Building encoder and decoder ...
Models built and ready to go!


In [0]:
clip = 50.0
teacher_forcing_ratio = 1.0
learning_rate = 0.0001
decoder_learning_ratio = 5.0
n_iteration = 3500
print_every = 1
save_every = 500
corpus_name = "cornell movie-dialogs corpus"
corpus = os.path.join(root_path, corpus_name)


# Ensure dropout layers are in train mode
encoder.train()
decoder.train()

# Initialize optimizers
print('Building optimizers ...')
encoder_optimizer = optim.Adam(encoder.parameters(), lr=learning_rate)
decoder_optimizer = optim.Adam(decoder.parameters(), lr=learning_rate * decoder_learning_ratio)
if loadFilename:
    encoder_optimizer.load_state_dict(encoder_optimizer_sd)
    decoder_optimizer.load_state_dict(decoder_optimizer_sd)

# If you have cuda, configure cuda to call
for state in encoder_optimizer.state.values():
    for k, v in state.items():
        if isinstance(v, torch.Tensor):
            state[k] = v.cuda()

for state in decoder_optimizer.state.values():
    for k, v in state.items():
        if isinstance(v, torch.Tensor):
            state[k] = v.cuda()

# Run training iterations
print("Starting Training!")
trainIters(model_name, voc, pairs, encoder, decoder, encoder_optimizer, decoder_optimizer,
           embedding, encoder_n_layers, decoder_n_layers, save_dir, n_iteration, batch_size,
           print_every, save_every, clip, corpus, loadFilename)

Building optimizers ...
Starting Training!
Initializing ...
Training...
Iteration: 1; Percent complete: 0.0%; Average loss: 8.9643
Iteration: 2; Percent complete: 0.1%; Average loss: 8.8209


/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,plea

Iteration: 3; Percent complete: 0.1%; Average loss: 8.6372
Iteration: 4; Percent complete: 0.1%; Average loss: 8.3081
Iteration: 5; Percent complete: 0.1%; Average loss: 7.8505


/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,plea

Iteration: 6; Percent complete: 0.1%; Average loss: 7.3715
Iteration: 7; Percent complete: 0.2%; Average loss: 6.9074
Iteration: 8; Percent complete: 0.2%; Average loss: 6.7292


...

Iteration: 3993; Percent complete: 99.8%; Average loss: 2.5721
Iteration: 3994; Percent complete: 99.9%; Average loss: 2.6372
Iteration: 3995; Percent complete: 99.9%; Average loss: 2.7074


/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,plea

Iteration: 3996; Percent complete: 99.9%; Average loss: 2.6583
Iteration: 3997; Percent complete: 99.9%; Average loss: 2.6170
Iteration: 3998; Percent complete: 100.0%; Average loss: 2.3445


/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
/pytorch/aten/src/ATen/native/cuda/LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,plea

Iteration: 3999; Percent complete: 100.0%; Average loss: 2.7934
Iteration: 4000; Percent complete: 100.0%; Average loss: 2.6749


In [0]:
encoder.eval()
decoder.eval()

# Initialize search module
searcher = GreedySearchDecoder(encoder, decoder)

# Begin chatting (uncomment and run the following line to begin)
evaluateInput(encoder, decoder, searcher, voc)

> 
Bot: what ? ? ! ! !
> hi
Bot: hi . . . . .
> how are you??
Bot: i m fine . . . .
> good
Bot: good . . . .
> what are you?
Bot: i m going to see you . .
> you are soo sweet
Error: Encountered unknown word.
> bye
Bot: bye . . . . .


KeyboardInterrupt: ignored